# Linear Programming in Python

## Part 1: Overview and Mathematical Formulation

A civil engineering company wants to decide on the projects that they should do. Their objective is to minimize the environmental impact of their projects while making enough profit to keep the company running.

They have a portfolio of 6 possible projects to invest in, where A, B , and C are new infrastructure projects (so-called type 1), and D, E, F are refurbishment projects (so-called type 2).

The environmental impact of each project is given by $I_i$ where $i \in [1,(...),6]$ is the index of the project. $I_i=[90,45,78,123,48,60]$

The profit of each project is given by $P_i$ where $i\in [1,(...),6]$ is the index of the project: $P_i=[120,65,99,110,33,99]$

The company is operating with the following constraints, please formulate the mathematical program that allows solving the problem:

- The company wants to do 3 out of the 6 projects
- the projects of type 2 must be at least as many as the ones of type 1 
- the profit of all projects together must be greater or equal than $250$ ($\beta$)

<div style="background-color:#AABAB2; color: black; width:95%; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px">
<p>

<b>Task 1: Writing the mathematical formulation</b>   

Write down every formulation and constraint that is relevant to solve this optimization problem.
  
</p>
</div>

<div style="background-color:#FAE99E; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<b>Solution</b>

$$
Min(Z) \sum_{i=1}^{6} x_i I_i 
$$

subject to

$$ \sum_{i=1}^{6} x_i = 3 $$
$$ \sum_{i=4}^{6} x_i \ge \sum_{i=1}^{3} x_i $$
$$ \sum_{i=1}^{6} x_i P_i \ge β $$
$$x\in(1,0), i\in(1,....,6)$$
    
The constraint related to: Extra Challenge (Task 6)
$$ \sum_{i=1}^{6} x_i I_i \le x_1 γ + (1-x_1) M $$
    
where M is a sufficiently big number such as 9999
</div>



<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<p>
<b>Task 2: Setting up the software</b>   
<br>
    
We will use <b>Pyomo</b> (modeling language) together with the open-source solver <b>HiGHS</b>.
No licenses are required.
</p>

<p><b>What you need:</b></p>
<ul>
<li>Python environment (same as previous weeks)</li>
<li>Install the packages: pyomo and highspy</li>
</ul>

<p><b>Installation (if needed):</b></p>
<pre>
pip install pyomo highspy
</pre>

</div>

In [1]:
from pyomo.environ import (
    ConcreteModel, Set, Var, Param, Objective, Constraint,
    Binary, NonNegativeReals, Integers, minimize, maximize,
    SolverFactory, value
)

<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<p>
<b>Task 3: Setting up the problem</b>   

Define any inputs you might need to setup your model.
</p>
</div>

In [2]:
# Project data
I = [1, 2, 3, 4, 5, 6]   # project index set

impact = {1: 90,
          2: 45,
          3: 78,
          4: 123,
          5: 48,
          6: 60}

profit = {1: 120,
          2: 65,
          3: 99,
          4: 110,
          5: 33,
          6: 99}

# Minimum required profit
beta = 250
M = 100000 #Later

type1 = {1, 2, 3}    # type-1 projects
type2 = {4, 5, 6}    # type-2 projects

# Number of projects and types
num_projects = len(I)
num_type1 = len(type1)
num_type2 = len(type2)

## Part 2: Create model with Pyomo + HiGHS

We will follow these steps (Pyomo separates modeling from solving):

1. Define the model container (`ConcreteModel`)
2. Define sets and parameters (`Param` or Python Dictionary)
3. Define decision variables (`Var`)
4. Define the objective (`Objective`)
5. Add constraints (`Constraint`)
6. Call the solver (`SolverFactory("highs").solve(m, tee=False)`)

If you need help on a Pyomo component, use Python's help:
```
import pyomo.environ as pyo
help(pyo.Var)
```


<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<p>
<b>Task 4: Create the Pyomo model</b>   

Create the Pyomo model, declare the decision variables, objective function, and constraints
as specified in the formulation. Use the code skeleton provided to guide you. You can also refer to the [Pyomo](https://pyomo.readthedocs.io/en/stable/getting_started/pyomo_overview/simple_examples.html) documentation for additional details of implementation.

</p>
</div>

In [3]:
# Build the Pyomo model using the inputs from Task 3

m = ConcreteModel()

# Sets
m.I = Set(initialize=I)

# Decision variables
m.x = Var(m.I, domain=Binary)   # 1 if project i is selected

# Objective: minimize total environmental impact
m.obj = Objective(expr=sum(impact[i] * m.x[i] for i in m.I), sense=minimize)

# Constraints
# (1) Select exactly three projects
m.cardinality = Constraint(expr=sum(m.x[i] for i in m.I) == 3)

# (2) Type-2 projects ≥ Type-1 projects
m.type_balance = Constraint(
    expr=sum(m.x[i] for i in type2) >= sum(m.x[i] for i in type1)
)

# (3) Total profit ≥ beta
m.min_profit = Constraint(
    expr=sum(profit[i] * m.x[i] for i in m.I) >= beta
)

<div style="background-color:#FAE99E; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<p>
<b>Solution.</b><br><br>

<b>m = ConcreteModel()</b><br>
Creates the Pyomo model container. All sets, variables, objective, and constraints are attached to <code>m</code>.<br><br>

<b>m.I = Set(initialize=I)</b><br>
Declares the index set of projects using the data vector <code>I</code> defined in Task 3 (e.g., [1,2,3,4,5,6]).<br><br>

<b>m.x = Var(m.I, domain=Binary)</b><br>
Creates a binary decision variable for each project i ∈ I. <br>

<b>m.obj = Objective(..., sense=minimize)</b><br>
Defines the objective to <i>minimize total environmental impact</i><br>

<b>m.cardinality = Constraint(expr = sum(x[i] for i in I) == 3)</code></b><br>
Enforces that exactly three projects are selected in total<br>

<b>m.type_balance = Constraint(expr = sum(x[i] for i in type2) >= sum(x[i] for i in type1))</code></b><br>
Ensures at least as many type-2 projects as type-1 projects<br>

<b>m.min_profit = Constraint(expr = sum(profit[i] * x[i] for i in I) >= beta)</b><br>
Imposes the minimum profit requirement<br>

<i>Notes:</i> All parameters (<code>I</code>, <code>impact</code>, <code>profit</code>, <code>type1</code>, <code>type2</code>, <code>beta</code>) are defined in the Task 3 cell. Solving is executed in a later cell with <code>SolverFactory("highs").solve(m, tee=False)</code>.

</p>
</div>



<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<p>
<b>Task 5: Display your results</b>   

Display the model in a good way to interpret and print the solution of the optimization.
</p>
</div>

In [4]:
result = SolverFactory("highs").solve(m, tee=False)
print("Status:", result.solver.status)
print("Termination:", result.solver.termination_condition)

selected = [i for i in m.I if value(m.x[i]) > 0.5] 
total_profit = sum(profit[i] * value(m.x[i]) for i in m.I)
total_impact = sum(impact[i] * value(m.x[i]) for i in m.I)

print("\nSelected projects:", selected)
print("Total profit:", total_profit)
print("Total environmental impact:", total_impact)
print("Type-1 selected:", sum(value(m.x[i]) for i in type1))
print("Type-2 selected:", sum(value(m.x[i]) for i in type2))


Status: ok
Termination: optimal

Selected projects: [1, 5, 6]
Total profit: 252.0
Total environmental impact: 198.0
Type-1 selected: 1.0
Type-2 selected: 2.0


<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<p>
<b>Task 6: Additional constraint</b>   

Solve the model with an additional constraint: if project 1 is done then the impact of all projects together should be lower than $\gamma$ with $\gamma=130$.

In the first cell you should add the constraint, then in a second cell optimize the model.

</p>
</div>

In [5]:
gamma = 130
m.impact_conditional = Constraint(
    expr = sum(impact[i] * m.x[i] for i in m.I) <= m.x[1] * gamma + (1 - m.x[1]) * M
)

In [6]:
result2 = SolverFactory("highs").solve(m, tee=False)
print("Status:", result2.solver.status)
print("Termination:", result2.solver.termination_condition)

selected2 = [i for i in m.I if value(m.x[i]) > 0.5]
total_profit2 = sum(profit[i] * value(m.x[i]) for i in m.I)
total_impact2 = sum(impact[i] * value(m.x[i]) for i in m.I)

print("\nSelected projects (new):", selected2)
print("Total profit (new):", total_profit2)
print("Total environmental impact (new):", total_impact2)

Status: ok
Termination: optimal

Selected projects (new): [2, 4, 6]
Total profit (new): 274.0
Total environmental impact (new): 228.0


> By Nadia Pourmohammadzia, Delft University of Technology. CC BY 4.0, more info [on the Credits page of Workbook](https://mude.citg.tudelft.nl/workbook-2025/credits.html).